In [ ]:
!git clone https://github.com/google-research/google-research.git
!pip install tensorflow

# Download images

In [ ]:
# -*- coding: utf-8 -*-
import io
import json
from pathlib import Path
from typing import Any, Dict, List, Optional, Tuple

import tensorflow as tf
from PIL import Image

# =========================
# TF.Feature -> Python value conversion
# =========================
def feature_to_list_bytes(f: tf.train.Feature) -> List[bytes]:
    return list(f.bytes_list.value)

def feature_to_list_int(f: tf.train.Feature) -> List[int]:
    return list(f.int64_list.value)

def feature_to_list_float(f: tf.train.Feature) -> List[float]:
    return list(f.float_list.value)

def get_feature(example: tf.train.Example, key: str) -> Optional[tf.train.Feature]:
    fmap = example.features.feature
    return fmap[key] if key in fmap else None

# =========================
# Extract coordinates from action (supports both normalized/pixel)
# =========================
def extract_points_from_action(
    action: Dict[str, Any],
    img_w: int,
    img_h: int
) -> List[Tuple[int, int]]:
    """
    Returns: [(x_px, y_px), ...]
    - Single point (tap) returns length 1
    - Drag/swipe returns 2 points (start/end)
    - Empty list if no points
    """
    pts: List[Tuple[int, int]] = []

    def to_px(x: float, y: float, normalized: Optional[bool]=None) -> Tuple[int,int]:
        if normalized is None:
            normalized = (0.0 <= x <= 1.0 and 0.0 <= y <= 1.0)
        if normalized:
            return (int(round(x * img_w)), int(round(y * img_h)))
        else:
            return (int(round(x)), int(round(y)))

    # 1) Top-level x, y
    if "x" in action and "y" in action:
        pts.append(to_px(float(action["x"]), float(action["y"]), None))

    # 2) point / click / tap / press / long_press / long_tap
    for k in ["point", "click", "tap", "press", "long_press", "long_tap"]:
        if k in action and isinstance(action[k], dict):
            px = action[k]
            if "x" in px and "y" in px:
                pts.append(to_px(float(px["x"]), float(px["y"]), None))
        if k in action and isinstance(action[k], list):
            for px in action[k]:
                if isinstance(px, dict) and "x" in px and "y" in px:
                    pts.append(to_px(float(px["x"]), float(px["y"]), None))

    # 3) from/to, start/end
    for a, b in [("from", "to"), ("start", "end")]:
        if a in action and b in action and isinstance(action[a], dict) and isinstance(action[b], dict):
            ax, ay = action[a].get("x"), action[a].get("y")
            bx, by = action[b].get("x"), action[b].get("y")
            if ax is not None and ay is not None and bx is not None and by is not None:
                pts.append(to_px(float(ax), float(ay), None))
                pts.append(to_px(float(bx), float(by), None))

    # 4) start_x/start_y/end_x/end_y
    cand = {"start_x": None, "start_y": None, "end_x": None, "end_y": None}
    found = False
    for ck in cand.keys():
        if ck in action:
            cand[ck] = float(action[ck])
            found = True
    if found and cand["start_x"] is not None and cand["start_y"] is not None:
        pts.append(to_px(cand["start_x"], cand["start_y"], None))
        if cand["end_x"] is not None and cand["end_y"] is not None:
            pts.append(to_px(cand["end_x"], cand["end_y"], None))

    # Remove duplicates
    uniq: List[Tuple[int,int]] = []
    seen = set()
    for p in pts:
        if p not in seen:
            uniq.append(p)
            seen.add(p)
    return uniq

# =========================
# Parse episode from TF Example
# =========================
def load_episode_from_example(ex: tf.train.Example) -> Dict[str, Any]:
    f = ex.features.feature

    screenshots_bytes = feature_to_list_bytes(f["screenshots"])
    a11y_bytes_list = feature_to_list_bytes(f["accessibility_trees"])
    widths = feature_to_list_int(f["screenshot_widths"])
    heights = feature_to_list_int(f["screenshot_heights"])

    actions_json_list = [b.decode("utf-8") for b in feature_to_list_bytes(f["actions"])]
    step_insts = [b.decode("utf-8") for b in feature_to_list_bytes(f["step_instructions"])]
    actions = [json.loads(s) for s in actions_json_list]

    goal = f["goal"].bytes_list.value[0].decode("utf-8")
    episode_id = int(f["episode_id"].int64_list.value[0]) if f["episode_id"].int64_list.value else int(
        f["episode_id"].bytes_list.value[0].decode("utf-8")
    )

    assert len(screenshots_bytes) == len(widths) == len(heights), "screenshot/width/height length mismatch"
    assert len(actions) == len(step_insts) == (len(screenshots_bytes) - 1), \
        "actions/step_instructions must equal screenshots-1"

    return {
        "episode_id": episode_id,
        "goal": goal,
        "screenshots": screenshots_bytes,
        "a11y": a11y_bytes_list,
        "widths": widths,
        "heights": heights,
        "actions": actions,
        "step_instructions": step_insts,
    }

# =========================
# Action mapping & utilities
# =========================
def _center_xy(w: int, h: int) -> Tuple[int,int]:
    return (int(round(w/2)), int(round(h/2)))

def _norm_dir(d: Optional[str]) -> str:
    if not d: return "down"
    d = str(d).lower()
    if d in ["up","down","left","right"]:
        return d
    if d in ["u","top"]: return "up"
    if d in ["d","bottom"]: return "down"
    if d in ["l"]: return "left"
    if d in ["r"]: return "right"
    return "down"

def map_action(
    action: Dict[str, Any],
    w: int,
    h: int,
    pts: List[Tuple[int,int]],
) -> Optional[Dict[str, Any]]:
    """
    Allowed mappings:
    click -> {"type": "touch", "x": <x>, "y": <y>}
    long_press -> {"type": "long_touch", "x": <x>, "y": <y>}
    input_text -> {"type": "set_text", "text": "...", "x": <x>, "y": <y>}
    scroll -> {"type": "scroll", "direction": "up|down|left|right", "x": <center_x>, "y": <center_y>}
    navigate_home -> {"type": "press", "key": "home"}
    navigate_back -> {"type": "press", "key": "back"}
    """
    atype = (action.get("action_type") or action.get("type") or action.get("action") or "").lower()
    x, y = (pts[0] if pts else _center_xy(w, h))

    if atype in ["click", "tap", "press", "click_view"]:
        return {"type": "touch", "x": x, "y": y}

    if atype in ["long_press", "long_tap", "long_click"]:
        return {"type": "long_touch", "x": x, "y": y}

    if atype in ["input_text", "set_text", "type_text", "enter_text", "text"]:
        text = action.get("text") or action.get("input_text") or action.get("value") or ""
        return {"type": "set_text", "text": str(text), "x": x, "y": y}

    if atype in ["scroll", "swipe"]:
        if len(pts) >= 2:
            cx = (pts[0][0] + pts[1][0]) // 2
            cy = (pts[0][1] + pts[1][1]) // 2
        else:
            cx, cy = _center_xy(w, h)
        return {"type": "scroll", "direction": _norm_dir(action.get("direction")), "x": cx, "y": cy}

    if atype in ["navigate_home", "home", "press_home"]:
        return {"type": "press", "key": "home"}

    if atype in ["navigate_back", "back", "press_back"]:
        return {"type": "press", "key": "back"}

    # Others (open_app, wait, etc.) → skip saving
    return None

def save_clean_image(img_bytes: bytes, episode_id: int, step_idx: int, base_dir: str = "and_ctrl") -> str:
    """
    Save image as: out_episode_{EP}_step_{STEP:03d}.png (without overlay)
    """
    Path(base_dir).mkdir(parents=True, exist_ok=True)
    fname = f"out_episode_{episode_id}_step_{step_idx:03d}.png"
    fpath = Path(base_dir) / fname
    Image.open(io.BytesIO(img_bytes)).convert("RGB").save(fpath)
    # Return just the relative path from base_dir
    return f"{base_dir}/{fname}"

# =========================
# Export messages to JSON
# =========================
def export_messages(ds, limit_episodes: int = 5, out_json: str = "and_ctrl.json", image_dir: str = "and_ctrl"):
    """
    Extract allowed actions from first N episodes in TFRecordDataset
    and save them in request format to and_ctrl.json.
    """
    all_items: List[Dict[str, Any]] = []
    ep_cnt = 0

    for raw in ds:
        ex = tf.train.Example()
        ex.ParseFromString(raw.numpy())
        ep = load_episode_from_example(ex)

        ep_id = ep["episode_id"]
        for i, (action, inst) in enumerate(zip(ep["actions"], ep["step_instructions"])):
            w, h = ep["widths"][i], ep["heights"][i]
            img_bytes = ep["screenshots"][i]
            pts = extract_points_from_action(action, w, h)
            mapped = map_action(action, w, h, pts)
            if not mapped:
                continue  # Skip

            img_path = save_clean_image(img_bytes, ep_id, i, base_dir=image_dir)

            all_items.append({
                "messages": [
                    {"role": "user", "content": f"<image>\n{inst}"},
                    # Save as Python dict string (single quotes), not JSON
                    {"role": "assistant", "content": str(mapped)}
                ],
                "images": [img_path]
            })

        ep_cnt += 1
        if ep_cnt >= limit_episodes:
            break

    with open(out_json, "w", encoding="utf-8") as f:
        json.dump(all_items, f, ensure_ascii=False, indent=2)

    print(f"[DONE] episodes processed: {ep_cnt}, items saved: {len(all_items)} → {out_json}")

# =========================
# Main entry point
# =========================
def main():
    # Adjust path pattern if needed
    filenames = tf.io.gfile.glob('gs://gresearch/android_control/android_control*')
    ds = tf.data.TFRecordDataset(filenames, compression_type='GZIP')
    export_messages(ds, limit_episodes=50, out_json="and_ctrl.json", image_dir="and_ctrl")

if __name__ == "__main__":
    main()

In [ ]:
!gsutil du -sh gs://gresearch/android_control/android_control*


46.5 GiB     gs://gresearch/android_control/android_control*
